## 1. Define functions for... 

* collecting real time data from binance futures markets for any timeframe and numbers of candlesticks (1000 max)
* calculating support and resistance 

In [1]:
def collect_data(timeframe='4h', limit=500):
    # This function downloads candlestick data from
    # binance futures market

    # define the market
    exchange_f = ccxt.binance({
        'enableRateLimit': True,
        'options': {
            'defaultType': 'future',  # or 'margin'
        }})

    all_coins_f = list(exchange_f.load_markets().keys())

    coins = [x for x in all_coins_f if "BUSD" not in x]
    coins = [x for x in coins if "_" not in x]

    all_candles_f = []
    for symbol in coins:
        df = pd.DataFrame(exchange_f.fetch_ohlcv(symbol, timeframe=timeframe, limit=limit))
        df['symbol'] = symbol

        df.columns = ['Datetime', 'Open', 'High', 'Low', 'Close', 'Vol', 'Symbol']

        df['Datetime'] = df['Datetime'].apply(
            lambda x: time.strftime('%Y-%m-%d %H:%M:%S', time.gmtime(x / 1000.)))
        all_candles_f.append(df)

    all_candles_f = pd.concat(all_candles_f)

    return all_candles_f

def detect_levels(df):
    s =  np.mean(df['High'] - df['Low'])

    def isSupport(df,i):
      support = df['Low'][i] < df['Low'][i-1]  and df['Low'][i] < df['Low'][i+1] and df['Low'][i+1] < df['Low'][i+2] and df['Low'][i-1] < df['Low'][i-2]
      return support
    def isResistance(df,i):
      resistance = df['High'][i] > df['High'][i-1]  and df['High'][i] > df['High'][i+1] and df['High'][i+1] > df['High'][i+2] and df['High'][i-1] > df['High'][i-2]
      return resistance

    def isFarFromLevel(l):
       return np.sum([abs(l-x) < s  for x in levels]) == 0

    levels = []
    for i in range(2,df.shape[0]-2):
      if isSupport(df,i):
        l = df['Low'][i]
        if isFarFromLevel(l):
          levels.append((i,l))
      elif isResistance(df,i):
        l = df['High'][i]
        if isFarFromLevel(l):
          levels.append((i,l))
    return levels

## 2. Apply functions in practice

In [2]:
import numpy as np
import pandas as pd
import ccxt
import time
import dateutil
from datetime import datetime
from functools import reduce
from scipy.signal import argrelextrema

import plotly.graph_objects as go

# Pull datafrom exchange
data = collect_data(timeframe = '1d', limit = 500)

In [4]:
for i in data['Symbol'].unique().tolist():
    print(i)
    df = data[data['Symbol'] == i].tail(100)
    df = df.reset_index()
    
    levels = detect_levels(df)
    times = []
    prices = []
    for level in levels:
        time = df['Datetime'][level[0]]
        price = level[1]
        times.append(time)
        prices.append(price)

    test = pd.DataFrame(data = {'levels':prices, 'dates':times})

    print(test)
    candlestick = go.Candlestick(x=df['Datetime'], open=df['Open'], high=df['High'], low=df['Low'],
                                 close=df['Close'])

    fig = go.Figure(data=[candlestick])

    for row in test.iterrows():
        fig.add_shape(type="line", x0= row[1]['dates'], 
                                y0 = row[1]['levels'],
                                x1 = test.dates.max(),
                                y1 = row[1]['levels'], fillcolor = 'yellow')
    
    fig.layout.xaxis.type = 'category'

    fig.update_layout(
        width=800,
        height=600)

    fig.layout.xaxis.rangeslider.visible = False
    fig.show()

BTC/USDT
     levels                dates
0  57550.00  2021-10-28 00:00:00
1  64349.55  2021-11-02 00:00:00
2  69198.70  2021-11-10 00:00:00
3  51929.00  2021-12-07 00:00:00
4  45650.00  2021-12-31 00:00:00
5  41666.00  2022-01-14 00:00:00


ETH/USDT
   levels                dates
0  4145.0  2021-11-01 00:00:00
1  4676.0  2021-11-03 00:00:00
2  3580.0  2021-12-30 00:00:00


BCH/USDT
   levels                dates
0  520.81  2021-10-27 00:00:00
1  732.03  2021-11-09 00:00:00
2  686.10  2021-11-15 00:00:00
3  636.35  2021-11-25 00:00:00
4  587.56  2021-11-30 00:00:00
5  454.02  2021-12-16 00:00:00
6  419.04  2021-12-31 00:00:00


XRP/USDT
   levels                dates
0  1.1662  2021-10-21 00:00:00
1  1.2602  2021-11-04 00:00:00
2  1.0950  2021-11-06 00:00:00
3  0.9340  2021-12-09 00:00:00
4  1.0185  2021-12-23 00:00:00
5  0.8016  2021-12-30 00:00:00


EOS/USDT
   levels                dates
0   4.959  2021-10-21 00:00:00
1   3.750  2021-10-27 00:00:00
2   4.385  2021-11-21 00:00:00
3   2.956  2021-12-30 00:00:00


...

PEOPLE/USDT
    levels                dates
0  0.10443  2021-12-30 00:00:00
1  0.13434  2021-12-31 00:00:00
2  0.07129  2022-01-11 00:00:00
3  0.08800  2022-01-13 00:00:00


ANT/USDT
   levels                dates
0   9.692  2022-01-12 00:00:00


ROSE/USDT
    levels                dates
0  0.30303  2022-01-10 00:00:00
1  0.59443  2022-01-15 00:00:00


DUSK/USDT
    levels                dates
0  0.55000  2022-01-11 00:00:00
1  1.07711  2022-01-17 00:00:00


1000BTTC/USDT
Empty DataFrame
Columns: [levels, dates]
Index: []
